In [1]:
from binance.client import Client
from binance import ThreadedWebsocketManager
import binance as bn
import pandas as pd
import sys
from datetime import datetime, timedelta
import ta as ta
import numpy as np
import json
import sys
sys.path.append('C:\\Users\\Administrator\\Desktop\\utils')
import utils
import matplotlib.pyplot as plt
import smtplib
import time
import json

In [17]:
class Futures_trader():
    """
    Class to perform live testing using Binance Futures testnet stream of data
    """ 
    def __init__(self, symbol=None, units='0.006', interval=None, ema_slow=None, ema_fast=None, ema_signal=None, sma_slow=None, sma_fast=None, sl=None, tp=None, leverage=2, bot_name='macd_sma', testnet=None, assigned_duration_minutes=None, assigned_emergency_price_chg_pu=None):
        """
        :param symbol: ticker in Binance, i.e. "BTCUSDT"
        :type symbol: str.
        ----
        :param units: amount of base units, i.e. "BTC"
        :param type: float.
        ----
        :param interval: a string among the followings: ["1m", "3m", "5m", "15m", "30m", "1h", "2h", "4h", "6h", "8h", "12h", "1d", "3d", "1w", "1M"]
        :type interval: str.
        ----
        :param ema_slow: EMA slow for MACD calculation
        :type ema_slow: int.
        ----
        :param ema_fast: EMA fast for MACD calculation
        :type ema_fast: int.
        ----
        :param ema_signal: EMA signal for MACD calculation
        :type ema_signal: int.
        ----
        :param sma_slow: SMA slow signal for sma cross calculation
        :type sma_slow: int.
        ----        
        :param sma_fast: SMA fast signal for sma cross calculation
        :type sma_fast: int.
        ----            
        :param sl: per unit of closing price to execute stop loss
        :type sl: float
        ----
        :param tp: per unit of closing price to execute take profit
        :type tp: float
        ----
        :param leverage: leverage to use
        :type leverage: integer
        ----
        :param bot_name: name of the current strategy
        :type bot_name: string
        ---
        :param testnet: if True, testnet is used, otherwise REAL Binance account
        :type testnet: bool.
        ----
        :param assigned_duration_minutes: amount of minutes that the sesion is expected to last, if no problems appear.
        :type assigned_duration_minutes: int.
        ----
        :param: assigned_emergency_price_chg_pu: per unit threshold (in absolute value) above which a sell order will be executed for safety purposes.
        In the case of a price increase the pct is taken as double of the value introduced (ratio 2 win : 1 lose)
        :type assigned_emergency_price_chg_pu: float
        """
        self.units = units
        self.symbol = symbol
        self.interval = interval
        self.ema_slow = ema_slow
        self.ema_fast = ema_fast
        self.ema_signal = ema_signal 
        self.sma_slow = sma_slow
        self.sma_fast = sma_fast
        self.sl = sl
        self.tp = tp
        self.leverage = leverage
        self.bot_name = bot_name
        self.testnet = testnet 
        self.assigned_duration_minutes = assigned_duration_minutes
        self.run_end_time_utc = None #time in UTC when the calculation finished
        self.run_end_delta = None #amount of time that has passed since the beginning of the calculation
        self.data = pd.DataFrame() #initialized dataframe to contain all OHLC data
        self.orders = 0 #counter of the number of orders
        self.position = None #initially no position is decided, it is pending to analysis recent data of macd to decide if it is long (1), neutral (0) or no position ('np')
        self.client = None #Binance client
        self.trade_start_time_utc = None # time in utc to be defined when the stream of OHLC starts ( this time
        self.twm = None # Initialize ws client
        self.cum_profits = 0 #accumulated profits in the trading sesion
        
        self.initialize_emergency_price_parameters(assigned_emergency_price_chg_pu)
        
        self.conn = None #smtp connection
        #self.login_mail() #initialize smtp google account
        self.kline_tlast = None #date of latest kandle complete to use in define_strategy()
        
    def start_trading(self):
        #self.client.futures_change_margin_type(symbol = "BTCUSDT", marginType = "CROSSED")    def start_trading(self):
        self.trade_start_time_utc = datetime.utcnow()
        self.prepare_recent_data()
        self.client.futures_change_leverage(symbol = "BTCUSDT", leverage = self.leverage) #initialize leverage        
        self.init_socket()
        
    def init_socket(self):
        self.twm = ThreadedWebsocketManager()
        self.twm.start() 
        try:                  
            self.twm.start_kline_futures_socket(callback = self.stream_candles, symbol = self.symbol, interval = self.interval)
        except (BinanceAPIException, ConnectionResetError, requests.exceptions.ConnectionError, requests.exceptions.RequestException) as e:
            print(e)
            print('Something went wrong. Error occured at %s. The sesions will be automatically stopped after GOING NEUTRAL.' % (datetime.now().astimezone(timezone.utc)))
            self.stop_ses()

    def stream_candles(self, msg):
        event_time = pd.to_datetime(msg["E"], unit = "ms")
        start_time = pd.to_datetime(msg["k"]["t"], unit = "ms")
        self.kline_tlast = start_time #latest kandle date, complete or incomplete
        first   = float(msg["k"]["o"])
        high    = float(msg["k"]["h"])
        low     = float(msg["k"]["l"])
        close   = float(msg["k"]["c"])
        volume  = float(msg["k"]["v"])
        complete=       msg["k"]["x"]
    
        # feed df (add new bar / update latest bar)
        self.data.loc[start_time, 'Open'] = first
        self.data.loc[start_time, 'High'] = high
        self.data.loc[start_time, 'Low'] = low
        self.data.loc[start_time, 'Close'] = close
        self.data.loc[start_time, 'Volume'] = volume
        self.data.loc[start_time, 'Complete'] = complete
        #update MACD parameters with each ws retrieval
        macd_diff = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd_diff()
        macd_macd = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd()
        macd_signal = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd_signal()         
        #assigning the macd values to ticker dataframe
        self.data.loc[start_time, 'macd_diff'] = macd_diff.iloc[-1]
        self.data.loc[start_time, 'macd_macd'] = macd_macd.iloc[-1]
        self.data.loc[start_time, 'macd_signal'] = macd_signal.iloc[-1]
        #update SMAs with each ws retrieval
        sma_fast_ps = ta.trend.SMAIndicator(close=self.data.Close, window=self.sma_fast, fillna=False).sma_indicator()
        sma_slow_ps = ta.trend.SMAIndicator(close=self.data.Close, window=self.sma_slow, fillna=False).sma_indicator()
        #assigning the smas values to ticker dataframe
        self.data.loc[start_time, 'sma_fast_ps'] = sma_fast_ps.iloc[-1]
        self.data.loc[start_time, 'sma_slow_ps'] = sma_slow_ps.iloc[-1]
                
        print(".", end = "", flush = True) # just print something to get a feedback (everything OK)
        
        dt = datetime.utcnow() - self.trade_start_time_utc
        if ((dt) > timedelta(minutes=self.assigned_duration_minutes)):
            self.stop_ses()        
        
        if (self.assigned_emergency_price_chg_pu != None):
            self.run_emergency_price_check(close) # position is forced by this method without needing to call update_position
        
        if (complete == True and self.emergency_price_chg_flag==False):
            # if complete == False its necessary to wait till it is complete regardless of emergency_price_chg_flag value, since 
            # run_emergency_price_check() method handles the position when its True. When the flag will be changed to False after
            # the assessment finished, we come back to this branch.
            self.update_position()
            self.execute_trades()
        else:
            print(f"complete={complete} --- continuying the ws data retrieval till next complete=True kandle")
            
    def initialize_emergency_price_parameters(self, assigned_emergency_price_chg_pu=None):
        print('Executing initialize_emergency_price_parameters ...')
        self.assigned_emergency_price_chg_pu = assigned_emergency_price_chg_pu # positive threshold of returns to trigger emergency price change method
        self.close_pair = [] #two consecutive "close" prices to implement emergency price algorithm
        self.emergency_price_chg_flag = False #flag to activate the signal
        self.emergency_msg = None #message to be sent when emergency price signal activated
        self.pu_price_chg = None #percetatge of change in price monitored every second
        self.increase_counter = 0 #counter to monitor consecutive sharp increases in price per second
        self.decrease_counter = 0 #counter to monitor consecutive sharp decreases in price per second       

    def run_emergency_price_check(self, close=None):
        print('Executing run_emergency_price_check ...')
        if (len(self.close_pair) == 0):
            self.close_pair.append(close)
            return # there are not yet 2 values in the array to start the algo (self.pu_chg_flag is still "None")
        
        
        if (len(self.close_pair) == 1):
            self.close_pair.insert(0,close)
            self.pu_price_chg = ((self.close_pair[1]/self.close_pair[0])-1)
        elif (len(self.close_pair) == 2):
            self.close_pair.pop()
            self.close_pair.insert(0,close)
            self.pu_price_chg = ((self.close_pair[1]/self.close_pair[0])-1)
            # condition for emergency price increase
            if (self.pu_price_chg > 2 * self.assigned_emergency_price_chg_pu):
                self.emergency_price_chg_flag = True
                self.decrease_counter = 0
                self.increase_counter += 1
                self.emergency_msg = f"PRICE CHANGE - INCREASE - {self.increase_counter}"
                print(self.emergency_msg)
                if (self.increase_counter < 3):
                    pass
                elif (self.increase_counter == 3):
                    self.emergency_position_eval_increase()                               
                    self.emergency_price_chg_flag = False
                    self.increase_counter = 0
                    self.end_socket()
                    time.sleep(45)
                    self.init_socket()
                else:
                    pass
                
            # condition for emergency price decrease                    
            elif (self.pu_price_chg < -1*self.assigned_emergency_price_chg_pu):
                self.emergency_price_chg_flag = True
                self.increase_counter = 0
                self.decrease_counter += 1
                self.emergency_msg = f"PRICE CHANGE - DECREASE - {self.decrease_counter}"
                print(self.emergency_msg)                
                if (self.decrease_counter < 3):
                    pass
                elif (self.decrease_counter == 3):
                    self.emergency_position_eval_decrease()
                    self.emergency_price_chg_flag = False
                    self.decrease_counter = 0
                    self.end_socket()
                    time.sleep(45)
                    self.init_socket()
                else:
                    pass
            # condition for no emergency price change        
            else:
                self.emergency_price_chg_flag = False
                self.increase_counter = 0
                self.decrease_counter = 0    
        else:
            raise Exception(f"len(self.close_pair)={len(self.close_pair)} --- Unexpected value")
    
    def prepare_recent_data(self):
        print('executing prepare_recent_data')
        '''
        :param start: a string with the following format ""%Y-%m-%d-%H:%M" .i.e. "2022-01-29-20:00"
        :type start: str.
        :param end: a string with the following format ""%Y-%m-%d-%H:%M" .i.e. "2022-02-29-20:00"
        :type end: str.
        '''
        #Prepare pre-data to the present moment with non NaN for the trading period (macd paramters ready)
        current_time_obj = datetime.now()
        current_time = int(current_time_obj.timestamp()*1000)
        
        #["1m", "3m", "5m", "15m", "30m", "1h", "2h", "4h", "6h", "8h", "12h", "1d", "3d", "1w", "1M"]
        extra_periods = 0
        ema_diff = self.ema_slow + self.ema_signal + 2
        
        # Necessary extra periods to have enough data to calculate the strategy parameters at the present moment
        if (ema_diff >= self.sma_slow):
            extra_periods = ema_diff * 2
        else:
            extra_periods = self.sma_slow * 2
        
        td = timedelta()
        if 'm' in self.interval:
            num_min = int(self.interval.replace('m',''))
            td = timedelta(minutes=num_min*(extra_periods))
        if 'h' in self.interval:
            num_h = int(self.interval.replace('h',''))
            td = timedelta(hours=num_h*(extra_periods))
        if 'd' in self.interval:
            num_day = int(self.interval.replace('d',''))
            td = timedelta(days=num_day*(extra_periods))
        if 'w' in self.interval:
            num_week = int(self.interval.replace('w',''))
            td = timedelta(weeks=num_week*(extra_periods))
        if 'M' in self.interval:
            num_week_m = int(self.interval.replace('M',''))
            td = timedelta(weeks=num_week_m * 4 * (extra_periods))

        from_time_obj = current_time_obj - td
        from_time = int((current_time_obj - td).timestamp()*1000)
        self.data, self.client = utils.futures_history(symbol=self.symbol, interval=self.interval, start=from_time, end=current_time, testnet=self.testnet)
        #obtaining MACD instance from python ta
        macd_diff = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd_diff()
        macd_macd = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd()
        macd_signal = ta.trend.MACD(close=self.data.Close, window_slow=self.ema_slow, window_fast=self.ema_fast, window_sign=self.ema_signal, fillna=False).macd_signal()
        #assigning the values of macd to ticker dataframe
        self.data['macd_diff'] = macd_diff
        self.data['macd_macd'] = macd_macd
        self.data['macd_signal'] = macd_signal
        #calculating SMA fast and slow
        sma_fast_ps = ta.trend.SMAIndicator(close=self.data.Close, window=self.sma_fast, fillna=False).sma_indicator()
        sma_slow_ps = ta.trend.SMAIndicator(close=self.data.Close, window=self.sma_slow, fillna=False).sma_indicator()
        #assigning the smas values to ticker dataframe
        self.data['sma_fast_ps'] = sma_fast_ps
        self.data['sma_slow_ps'] = sma_slow_ps
        #initialize dataframe columns for prepared data
        self.data['position'] = 0
        self.data['macd_inv_sign'] = 0
        self.data['sma_conf'] = 0
        self.data['sma_inv_sign'] = 0
        self.data['macd_diff_conf'] = 0
        if (self.sl != None and self.tp != None):
            self.data['sl_flag_short'] = None
            self.data['tp_flag_short'] = None
            self.data['sl_flag_long'] = None
            self.data['tp_flag_long'] = None
        else: 
            pass
        self.stablish_initial_position()
        self.data["Complete"] = [True for row in range(len(self.data)-1)] + [False]
        #decide position to be given to the latest recent data kandle (not completed in 99% of cases and that is 
        #going to be updated by the stream of data, so actually, position given to the latest kandle at this point
        #it is mots likely not to be used, but updated.
        
    def stablish_initial_position(self):
        print('executing stablish_initial_position')
        # --------------------- MACD CROSS SIGNAL + SMA CONFIRMATION ---------------------

        #macd cross short
        ht_macd_diff_pos = self.data.macd_diff.shift(1) > 0
        ht_macd_diff_plusone_neg = self.data.macd_diff < 0        
       
        #sma short confirmation
        sma_conf_short = self.data.sma_fast_ps < self.data.sma_slow_ps
        
        #stablish short positions
        self.data.loc[ht_macd_diff_pos & ht_macd_diff_plusone_neg, 'macd_inv_sign'] = -1
        self.data.loc[sma_conf_short, 'sma_conf'] = -1
        
        #macd cross long
        ht_macd_diff_neg = self.data.macd_diff.shift(1) < 0
        ht_macd_diff_plusone_pos = self.data.macd_diff > 0
        
        #sma long confirmation
        sma_conf_long = self.data.sma_fast_ps > self.data.sma_slow_ps        
        
        #stablish buy positions
        self.data.loc[ht_macd_diff_neg & ht_macd_diff_plusone_pos, 'macd_inv_sign'] = 1
        self.data.loc[sma_conf_long, 'sma_conf'] = 1
        
        # ---------------------------------------------------------------------------------
        
        # --------------------- SMA CROSS SIGNAL + MACD_DIFF CONFIRMATION -----------------
        
        #sma cross short
        ht_sma_pos = self.data.sma_fast_ps.shift(1) > self.data.sma_slow_ps.shift(1)
        ht_sma_plusone_neg = self.data.sma_fast_ps < self.data.sma_slow_ps
        
        #macd_diff short confirmation
        macd_diff_conf_short = self.data.macd_diff < 0
        
        #stablish short positions
        self.data.loc[ht_sma_pos & ht_sma_plusone_neg, 'sma_inv_sign'] = -1
        self.data.loc[macd_diff_conf_short, 'macd_diff_conf'] = -1
        
        #sma cross long
        ht_sma_neg = self.data.sma_fast_ps.shift(1) < self.data.sma_slow_ps.shift(1)
        ht_sma_plusone_pos = self.data.sma_fast_ps > self.data.sma_slow_ps        
        
        #macd_diff long confirmation
        macd_diff_conf_long = self.data.macd_diff > 0
        
        #stablish buy positions
        self.data.loc[ht_sma_neg & ht_sma_plusone_pos, 'sma_inv_sign'] = 1
        self.data.loc[macd_diff_conf_long, 'macd_diff_conf'] = 1        
        
        # ---------------------------------------------------------------------------------
        for index, data in self.data.iterrows():
            
            if ((data.macd_inv_sign == 1 and data.sma_inv_sign == 1) or (data.macd_inv_sign == 1 and data.sma_conf == 1)): #CHECKED
                self.data.loc[index, 'position'] = 1
                one_delta_pos = index + (self.data.index[1]-self.data.index[0])
                self.data_sub_buy = self.data.loc[one_delta_pos:]
                for index_sub_buy, data_sub_buy in self.data_sub_buy.iterrows():
                    # initialize flag in every loop
                    sltp_flag = False
                    if (self.sl != None and self.tp != None): # only if both are defined, it is then necessary to assess sl/tp
                        sl_flag = data_sub_buy.Close <= (data.Close * (1 - self.sl))  # condition for stop loss in sub loop
                        tp_flag = data_sub_buy.Close > (data.Close * (1 + self.tp)) # condition for take profit in sub loop
                        sltp_flag = sl_flag or tp_flag # flag once detected sl or tp, to stop the long position loop
                        self.data.loc[index_sub_buy,'sl_flag_long'] = sl_flag
                        self.data.loc[index_sub_buy,'tp_flag_long'] = tp_flag  
                        
                    if ((data.macd_inv_sign == -1 and data.sma_inv_sign == -1) or (data.macd_inv_sign == -1 and data.sma_conf == -1) or (data.sma_inv_sign == -1 and data.macd_diff_conf == -1) or sltp_flag == True):
                        break
                    else: 
                        self.data.loc[index_sub_buy, 'position'] = 1
                
            elif ((data.macd_inv_sign == -1 and data.sma_inv_sign == -1) or (data.macd_inv_sign == -1 and data.sma_conf == -1)): 
                self.data.loc[index, 'position'] = -1
                one_delta_pos = index + (self.data.index[1]-self.data.index[0])
                self.data_sub_sell = self.data.loc[one_delta_pos:]
                for index_sub_sell, data_sub_sell in self.data_sub_sell.iterrows():
                    # initialize flag in every loop
                    sltp_flag = False
                    if (self.sl != None and self.tp != None): # only if both are defined, it is then necessary to assess sl/tp
                        tp_flag = data_sub_sell.Close <= (data.Close * (1 - self.tp))  # condition for stop loss in sub loop
                        sl_flag = data_sub_sell.Close > (data.Close * (1 + self.sl)) # condition for take profit in sub loop
                        sltp_flag = sl_flag or tp_flag # flag once detected sl or tp, to stop the long position loop
                        self.data.loc[index_sub_sell,'sl_flag_short'] = sl_flag
                        self.data.loc[index_sub_sell,'tp_flag_short'] = tp_flag
                        
                    if ((data.macd_inv_sign == 1 and data.sma_inv_sign == 1) or (data.macd_inv_sign == 1 and data.sma_conf == 1) or (data.sma_inv_sign == 1 and data.macd_diff_conf == 1) or sltp_flag == True):
                        break
                    else:
                        self.data.loc[index_sub_sell, 'position'] = -1
                        
            elif ((data.sma_inv_sign == 1 and data.macd_inv_sign == 1) or (data.sma_inv_sign == 1 and data.macd_diff_conf == 1)): #CHECKED
                self.data.loc[index, 'position'] = 1
                one_delta_pos = index + (self.data.index[1]-self.data.index[0])
                self.data_sub_buy = self.data.loc[one_delta_pos:]
                for index_sub_buy, data_sub_buy in self.data_sub_buy.iterrows():
                    # initialize flag in every loop
                    sltp_flag = False
                    if (self.sl != None and self.tp != None): # only if both are defined, it is then necessary to assess sl/tp
                        sl_flag = data_sub_buy.Close <= (data.Close * (1 - self.sl))  # condition for stop loss in sub loop
                        tp_flag = data_sub_buy.Close > (data.Close * (1 + self.tp)) # condition for take profit in sub loop
                        sltp_flag = sl_flag or tp_flag # flag once detected sl or tp, to stop the long position loop
                        self.data.loc[index_sub_buy,'sl_flag_long'] = sl_flag
                        self.data.loc[index_sub_buy,'tp_flag_long'] = tp_flag                                            
                    if ((data.sma_inv_sign == -1 and data.macd_inv_sign == -1) or (data.sma_inv_sign == -1 and data.macd_diff_conf == -1) or (data.macd_inv_sign == -1 and data.sma_conf == -1) or sltp_flag == True):
                        break
                    else:
                        self.data.loc[index_sub_buy, 'position'] = 1
                
            elif ((data.sma_inv_sign == -1 and data.macd_inv_sign == -1) or (data.sma_inv_sign == -1 and data.macd_diff_conf == -1)):
                self.data.loc[index, 'position'] = -1
                one_delta_pos = index + (self.data.index[1]-self.data.index[0])
                self.data_sub_sell = self.data.loc[one_delta_pos:]
                for index_sub_sell, data_sub_sell in self.data_sub_sell.iterrows():
                    # initialize flag in every loop
                    sltp_flag = False
                    if (self.sl != None and self.tp != None): # only if both are defined, it is then necessary to assess sl/tp
                        tp_flag = data_sub_sell.Close <= (data.Close * (1 - self.tp))  # condition for stop loss in sub loop
                        sl_flag = data_sub_sell.Close > (data.Close * (1 + self.sl)) # condition for take profit in sub loop
                        sltp_flag = sl_flag or tp_flag # flag once detected sl or tp, to stop the long position loop
                        self.data.loc[index_sub_sell,'sl_flag_short'] = sl_flag
                        self.data.loc[index_sub_sell,'tp_flag_short'] = tp_flag
                        
                    if ((data.sma_inv_sign == 1 and data.macd_inv_sign == 1) or (data.sma_inv_sign == 1 and data.macd_diff_conf == 1) or (data.macd_inv_sign == 1 and data.sma_conf == 1)):
                        break
                    else:
                        self.data.loc[index_sub_sell, 'position'] = -1
            else:
                pass
            
        self.kline_tprev_complete = self.data.index[-2]
        
    def run_sltp_check(self, data_upd=None):
        print('executing run_sltp_check')
        tp_flag_short = data_upd.Close.loc[klast] <= (data_upd.Close.loc[kprev] * (1 - self.tp)) # condition for stop loss in short position ### ERROR HERE WHILE STREAMING
        sl_flag_short = data_upd.Close.loc[klast] > (data_upd.Close.loc[kprev] * (1 + self.sl)) # condition for take profit in short position       

        if (data_upd.position.loc[kprev] == -1):
            if (tp_flag_short):
                data_upd.loc[klast, 'tp_flag_short'] = True
                data_upd.loc[klast, 'sl_flag_short'] = False
                data_upd.loc[klast, 'position'] = 0
            elif sl_flag_short:
                data_upd.loc[klast, 'sl_flag_short'] = True
                data_upd.loc[klast, 'tp_flag_short'] = False
                data_upd.loc[klast, 'position'] = 0
                return
            else:
                data_upd.loc[klast, 'sl_flag_short'] = None
                data_upd.loc[klast, 'tp_flag_short'] = None

        tp_flag_long = data_upd.Close.loc[klast] >= (data_upd.Close.loc[kprev] * (1 + self.tp)) # condition for stop loss in long position
        sl_flag_long = data_upd.Close.loc[klast] < (data_upd.Close.loc[kprev] * (1 - self.sl)) # condition for take profit in long position   
        if (data_upd.position.loc[kprev] == 1):
            if (tp_flag_long):
                data_upd.loc[klast, 'tp_flag_long'] = True
                data_upd.loc[klast, 'sl_flag_long'] = False
                data_upd.loc[klast, 'position'] = 0
            elif sl_flag_long:
                data_upd.loc[klast, 'sl_flag_long'] = True
                data_upd.loc[klast, 'tp_flag_long'] = False
                data_upd.loc[klast, 'position'] = 0
                return
            else:
                data_upd.loc[klast, 'sl_flag_long'] = None
                data_upd.loc[klast, 'tp_flag_long'] = None
    
    def update_position(self):
        print('executing update_position')
        data_upd = self.data.copy()
        
        td = timedelta()
        if 'm' in self.interval:
            num_min = int(self.interval.replace('m',''))
            td = timedelta(minutes=num_min)
        if 'h' in self.interval:
            num_h = int(self.interval.replace('h',''))
            td = timedelta(hours=num_h)
        if 'd' in self.interval:
            num_day = int(self.interval.replace('d',''))
            td = timedelta(days=num_day)
        if 'w' in self.interval:
            num_week = int(self.interval.replace('w',''))
            td = timedelta(weeks=num_week)
        if 'M' in self.interval:
            num_week_m = int(self.interval.replace('M',''))
            td = timedelta(weeks=4*num_week)
        
        kprev = self.kline_tlast - td 
        klast = self.kline_tlast
        self.kline_tprev_complete = kprev # to use in execute_trades() to assess long/short continuity or going out of a neutral position
        print(f"klast = self.kline_tlast /// klast = {self.kline_tlast}")
        print(f"kprev = (self.kline_tlast - td) /// kprev = {self.kline_tlast - td}")
        
        # ASSESSING STOP LOSS OR TAKE PROFIT TAKE PRECENDENCE, AND IF A CONDITION IS MET THE FUNCTION RETURNS
        
        if (self.sl != None and self.tp != None):
            self.run_sltp_check(df=data_upd)

        # --------------------- MACD CROSS SIGNAL + SMA CONFIRMATION ---------------------
        
        #macd cross long
        ht_macd_diff_neg = data_upd.macd_diff.loc[kprev] < 0
        ht_macd_diff_plusone_pos = data_upd.macd_diff.loc[klast] > 0        
        #macd cross short
        ht_macd_diff_pos = data_upd.macd_diff.loc[kprev] > 0
        ht_macd_diff_plusone_neg = data_upd.macd_diff.loc[klast] < 0 
    
        if (ht_macd_diff_neg and ht_macd_diff_plusone_pos):
            data_upd.loc[klast, 'macd_inv_sign'] = 1
        elif (ht_macd_diff_pos and ht_macd_diff_plusone_neg):
            data_upd.loc[klast, 'macd_inv_sign'] = -1
        else:
            data_upd.loc[klast, 'macd_inv_sign'] = 0
        
        #sma long confirmation
        sma_conf_long = data_upd.sma_fast_ps.loc[klast] > data_upd.sma_slow_ps.loc[klast]
        #sma short confirmation
        sma_conf_short = data_upd.sma_fast_ps.loc[klast] < data_upd.sma_slow_ps.loc[klast]
        if sma_conf_long:
            data_upd.loc[klast, 'sma_conf'] = 1
        elif sma_conf_short:
            data_upd.loc[klast, 'sma_conf'] = -1
        else:
            data_upd.loc[klast, 'sma_conf'] = 0
        
        # ---------------------------------------------------------------------------------
        
        # --------------------- SMA CROSS SIGNAL + MACD_DIFF CONFIRMATION -----------------

        #sma cross long
        ht_sma_neg = data_upd.sma_fast_ps.loc[kprev] < data_upd.sma_slow_ps.loc[kprev]
        ht_sma_plusone_pos = data_upd.sma_fast_ps.loc[klast] > data_upd.sma_slow_ps.loc[klast]        
        #sma cross short
        ht_sma_pos = data_upd.sma_fast_ps.loc[kprev] > data_upd.sma_slow_ps.loc[kprev]
        ht_sma_plusone_neg = data_upd.sma_fast_ps.loc[klast] < data_upd.sma_slow_ps.loc[klast]
                                                                                        
        if (ht_sma_neg and ht_sma_plusone_pos):
            data_upd.loc[klast, 'sma_inv_sign'] = 1
        elif (ht_sma_pos and ht_sma_plusone_neg):
            data_upd.loc[klast, 'sma_inv_sign'] = -1
        else:
            data_upd.loc[klast, 'sma_inv_sign'] = 0
                                                                                    

        #macd_diff short confirmation
        macd_diff_conf_short = data_upd.loc[klast, 'macd_diff'] < 0
        #macd_diff long confirmation
        macd_diff_conf_long = data_upd.loc[klast, 'macd_diff'] > 0
                                                                                        
        if macd_diff_conf_long:
            data_upd.loc[klast, 'macd_diff_conf'] = 1
        elif macd_diff_conf_short:
            data_upd.loc[klast, 'macd_diff_conf'] = -1
        else:
            data_upd.loc[klast, 'macd_diff_conf'] = 0
        
        # -------------------------------- POSITION DEFINITION -----------------------------
        
        if ((data_upd.loc[klast, 'macd_inv_sign'] == 1 and data_upd.loc[klast, 'sma_inv_sign'] == 1) or (data_upd.loc[klast, 'macd_inv_sign'] == 1 and data_upd.loc[klast, 'sma_conf'] == 1)):
            data_upd.loc[klast, 'position'] = 1
        
        elif ((data_upd.loc[klast, 'macd_inv_sign'] == -1 and data_upd.loc[klast, 'sma_inv_sign'] == -1) or (data_upd.loc[klast, 'macd_inv_sign'] == -1 and data_upd.loc[klast, 'sma_conf'] == -1)):
            data_upd.loc[klast, 'position'] = -1
        
        elif ((data_upd.loc[klast, 'sma_inv_sign'] == 1 and data_upd.loc[klast, 'macd_inv_sign'] == 1) or (data_upd.loc[klast, 'sma_inv_sign'] == 1 and data_upd.loc[klast, 'macd_diff_conf'] == 1)):
            data_upd.loc[klast, 'position'] = 1
        
        elif ((data_upd.loc[klast, 'sma_inv_sign'] == -1 and data_upd.loc[klast, 'macd_inv_sign'] == -1) or (data_upd.loc[klast, 'sma_inv_sign'] == -1 and data_upd.loc[klast, 'macd_diff_conf'] == -1)):
            data_upd.loc[klast, 'position'] = -1
        
        else:
            data_upd.loc[klast, 'position'] = 0
            
        self.data = data_upd.copy()
    
    def execute_trades(self):
        print('executing execute_trades')
        kprev = self.kline_tprev_complete
        klast = self.kline_tlast         
        
        if self.data.loc[klast, 'position'] == 1: # if position is long -> go/stay long
            if self.data.loc[kprev, 'position'] == 0:
                order = self.client.futures_create_order(symbol = self.symbol, side = "BUY", type = "MARKET", quantity = self.units)
                self.report_trade(order, "GOING LONG")  
            elif self.data.loc[kprev, 'position'] == -1:
                if (self.orders == 0): # if it is first order after prepare_recent_data() it is not necessary to go neutral first.
                    order = self.client.futures_create_order(symbol = self.symbol, side = "BUY", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING LONG")   
                elif (self.orders > 0):
                    order = self.client.futures_create_order(symbol = self.symbol, side = "BUY", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING LONG (PASSING BY NEUTRAL FIRST)")
                    order = self.client.futures_create_order(symbol = self.symbol, side = "BUY", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING LONG (PASSING BY NEUTRAL FIRST)")                      
        elif self.data.loc[klast, 'position'] == 0: # if position is neutral -> go/stay neutral
            if (self.orders == 0): #no need to do anything if there is no order. This means is false neutral flag coming from prepare_recent_data() first iteration. Sesion has been stopped before any orders where placed.
                return
            if self.data.loc[kprev, 'position'] == 1: ####### ERROR HERE WHEN EXECUTING STOP_SES() (previous kandle to last does not exist for some reason)
                order = self.client.futures_create_order(symbol = self.symbol, side = "SELL", type = "MARKET", quantity = self.units)
                self.report_trade(order, "GOING NEUTRAL") 
            elif self.data.loc[kprev, 'position'] == -1:
                order = self.client.futures_create_order(symbol = self.symbol, side = "BUY", type = "MARKET", quantity = self.units)
                self.report_trade(order, "GOING NEUTRAL")
        if self.data.loc[klast, 'position'] == -1: # if position is short -> go/stay short               
            if self.data.loc[kprev, 'position'] == 0:
                order = self.client.futures_create_order(symbol = self.symbol, side = "SELL", type = "MARKET", quantity = self.units)
                self.report_trade(order, "GOING SHORT") 
            elif self.data.loc[kprev, 'position'] == 1:
                if (self.orders == 0): # if it is first order after prepare_recent_data() it is not necessary to go neutral first.
                    order = self.client.futures_create_order(symbol = self.symbol, side = "SELL", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING SHORT")
                elif (self.orders > 0):
                    order = self.client.futures_create_order(symbol = self.symbol, side = "SELL", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING SHORT (PASSING BY NEUTRAL FIRST)")
                    order = self.client.futures_create_order(symbol = self.symbol, side = "SELL", type = "MARKET", quantity = self.units)
                    self.report_trade(order, "GOING SHORT (PASSING BY NEUTRAL FIRST)") 
                    
    def info_orders(self):
        pass
    
    def report_trade(self, order, going):
        print('executing report_trade')
        time.sleep(0.5)
        self.orders += 1
        order_time = order["updateTime"]
        trades = self.client.futures_account_trades(symbol = self.symbol, startTime = order_time)
        order_time = pd.to_datetime(order_time, unit = "ms")
        
        # extract data from order object
        df = pd.DataFrame(trades)
        columns = ["qty", "quoteQty", "commission","realizedPnl"]
        for column in columns:
            df[column] = pd.to_numeric(df[column], errors = "coerce")
        base_units = round(df.qty.sum(), 5)
        quote_units = round(df.quoteQty.sum(), 5)
        commission = -round(df.commission.sum(), 5)
        real_profit = round(df.realizedPnl.sum(), 5)
        price = round(quote_units / base_units, 5)
        
        # calculate cumulative trading profits
        self.cum_profits += round((commission + real_profit), 5)    
                 
        # print trade report
        print(2 * "\n" + 100* "-")
        msg1 = "{} | {}".format(order_time, going)
        print(msg1) 
        msg2 = "{} | Base_Units = {} | Quote_Units = {} | Price = {} ".format(order_time, base_units, quote_units, price)
        print(msg2)
        msg3 = "{} | Real profit = {} | Accumulate profit = {} ".format(order_time, real_profit, self.cum_profits)
        print(msg3)
        msg4 = ""
        
        if (self.emergency_price_chg_flag == True):
            msg4 = "price changed in 1s in pct: {}, which is more/less than the imposed pct: {} (imposed pct x2 if positive) ".format(round(self.pu_price_chg, 6), self.assigned_emergency_price_chg_pu) 
            print(msg4)
        print(100 * "-" + "\n")
#         mail_msg = f"Subject: trade executed. Bot name: {self.bot_name}. \n\n {msg1} \n\n {msg2} \n\n {msg3} \n\n {msg4}"
#         try:
#             self.conn.sendmail('jpxcar6@gmail.com', 'jpxcar6@gmail.com', f"{mail_msg}")
        
#         except (SMTPSenderRefused, SMTPSenderRefused, SMTPServerError, SMTPTimeoutError, SMTPError, SMTPServerDisconnected) as e:
#             print(e)
#             self.login_mail()
#             self.conn.sendmail('jpxcar6@gmail.com', 'jpxcar6@gmail.com', f"{mail_msg}")

    def emergency_position_eval_increase(self):
        # stablish long position before kandle is complete. Handle the position logic in execute_trades()
        klast = self.kline_tlast
        self.data.loc[klast, 'position'] = 1
        self.execute_trades()
            
    def emergency_position_eval_decrease(self):
        # stablish short position before kandle is complete. Handle the position logic in execute_trades()
        klast = self.kline_tlast
        self.data.loc[klast, 'position'] = -1
        self.execute_trades()

    def end_socket(self):
        self.twm.stop()
    
    def stop_ses(self, save_to_file=True):
        print('executing stop_ses')
        self.run_end_time_utc = datetime.utcnow()
        dt = self.run_end_time_utc - self.trade_start_time_utc
        self.run_end_delta = round(dt.seconds/60,0)
        print(f"trading sesion duration = {self.run_end_delta} minutes up to {self.assigned_duration_minutes}")
                            
        # stablish neutral position before kandle is complete. Handle the position logic in execute_trades()
        klast = self.kline_tlast
        self.data.loc[klast, 'position'] = 0
        if (self.orders != 0):
            self.execute_trades()
        else:
            pass
        print('SESION STOPPED')
        self.twm.stop()
        
        if (save_to_file == True):
            self.save_to_files()

    def plot_results(self, start_plot=None, end_plot=None, width_bars=0.1):
        # from IPython.core.display import display, HTML
        # display(HTML("<style>.container { width:100% !important; }</style>"))
        colors=[]

        fig, (close_ax, macd_ax) = plt.subplots(nrows=2, ncols=1, figsize=(30,20), gridspec_kw={'height_ratios': [4,2]}, sharex=True)

        close_ax.grid(visible=True, which='major', axis='x', color='grey')
        macd_ax.grid(visible=True, which='major', axis='x', color='grey')
        close_ax.grid(visible=True, which='major', axis='y', color='grey')
        macd_ax.grid(visible=True, which='major', axis='y', color='grey')
        close_ax.grid(visible=True, which='minor', axis='x', color='grey')
        macd_ax.grid(visible=True, which='minor', axis='x', color='grey')

        close_ax.tick_params(labelrotation=45, labelsize = 'large')
        macd_ax.tick_params(labelrotation=45, labelsize = 'large')

        close_ax.margins(0)
        macd_ax.margins(0)
        
        close_ax.set_ylim(auto=True)
        
        data_ready = self.data.dropna(subset=['macd_diff', 'macd_macd', 'macd_signal']).copy()
        
        
        if (start_plot == None):
            start_plot = data_ready.index[0]
        if (end_plot == None):
            end_plot = data_ready.index[-1]  
            
        if ((start_plot != None) and (end_plot !=None)):
            cond_start = data_ready.index >= start_plot
            cond_end = data_ready.index <= end_plot
            data_ready = data_ready[cond_start&cond_end]
                
        for index, value in data_ready.macd_diff.iteritems():
            if value > 0:
                colors.append('g')
            else:
                colors.append('r')
                
        close_ax.plot(data_ready.index, data_ready.Close) #plot the data without shifting

        #shift one position the inv_sign only for plotting the signal in the day after is found, without shifting the
        #Close prices
        data_ready_shift = data_ready.copy()
        data_ready_shift['position'] = data_ready.position.shift(1)
        long_pos = data_ready_shift.position == 1              
        long_trade = data_ready_shift.loc[long_pos]
        short_pos = data_ready_shift.position == -1            
        short_trade = data_ready_shift.loc[short_pos]
        close_ax.scatter(short_trade.index, short_trade.Close.loc[short_trade.index], marker='^', color='r', s=100)
        close_ax.scatter(long_trade.index, long_trade.Close.loc[long_trade.index], marker='^', color='g', s=100)

        if ((self.data.Complete.iloc[-1] == False) and (self.data.position.iloc[-1] == 0)):
            close_ax.scatter(self.data.index[-1], self.data.Close.loc[self.data.index[-1]], marker='^', color='r', s=100)
        
        macd_ax.bar(x= data_ready.index, height= data_ready.macd_diff, width=width_bars, align='center', color=colors, edgecolor='black')
    
    def save_to_files(self):
        print('executing save_to_files')
        file_name = f"{self.bot_name}__{self.symbol}__{self.interval}__eslow_{self.ema_slow}_efast_{self.ema_fast}_esign_{self.ema_signal}__smas_{self.sma_slow}__smaf_{self.sma_fast}__duration_{self.run_end_delta}min_upto_{self.assigned_duration_minutes}__ordersnum_{self.orders}" 
        outfile = open(file_name, 'wb')
        self.data.to_csv(outfile, index = True, header = True, sep = ',', encoding = 'utf-8', date_format ='%Y-%m-%d-%H:%M')
        outfile.close()
        results = {
            "units": self.units,
            "symbol": self.symbol,
            "interval": self.interval,
            "ema_slow": self.ema_slow,
            "ema_fast": self.ema_fast,
            "ema_signal": self.ema_signal,
            "sma_slow": self.sma_slow,
            "sma_fast": self.sma_fast,
            "sl": self.sl,
            "tp": self.tp,
            "leverage": self.leverage,
            "testnet": self.testnet,
            "assigned_duration_minutes": self.assigned_duration_minutes,
            "assigned_emergency_price_chg_pu": self.assigned_emergency_price_chg_pu,
            "run_end_time_utc": self.run_end_time_utc.strftime("%Y-%m-%d-%H:%M:%S"),
            "run_end_delta": self.run_end_delta,
            "orders": self.orders,
            "trade_start_time_utc": self.trade_start_time_utc.strftime("%Y-%m-%d-%H:%M:%S"),
            "profit": self.cum_profits,
            "emergency_price_chg_flag": self.emergency_price_chg_flag,
            "emergency_msg": self.emergency_msg,
            "pu_price_chg": self.pu_price_chg,
            "bot_name": self.bot_name  
        }
        f = open(f"{file_name}.txt", "a")
        json.dump(results, f)
        f.close()
    
#     def login_mail(self):
#         self.conn = smtplib.SMTP('smtp.gmail.com', 587)   
#         self.conn.ehlo()
#         self.conn.starttls()
#         self.conn.login('jpxcar6@gmail.com', 'iqdwckxxatmzbcom')
    
#     def logout_mail(self):
#         self.conn.quit()

In [18]:
pd.set_option('display.max_rows', None)

In [19]:

test_trader = Futures_trader(symbol='BTCUSDT', units='0.001', interval='1m', ema_slow=20, ema_fast=2, ema_signal=2, sma_slow=40, sma_fast=2, sl=None, tp=None, leverage=2, bot_name='futures_trader', testnet=True, assigned_duration_minutes=360, assigned_emergency_price_chg_pu=None)

Executing initialize_emergency_price_parameters ...


In [22]:
test_trader.data

Open     High      Low    Close   Volume  macd_diff  \
Date                                                                          
2022-11-27 15:01:00  16538.5  16538.5  16533.1  16534.7   37.049        NaN   
2022-11-27 15:02:00  16536.2  16538.5  16533.1  16537.1  118.346        NaN   
2022-11-27 15:03:00  16536.7  16537.6  16532.4  16534.5   46.869        NaN   
2022-11-27 15:04:00  16532.2  16538.1  16531.0  16536.5   95.360        NaN   
2022-11-27 15:05:00  16535.3  16535.3  16530.9  16530.9   40.256        NaN   
2022-11-27 15:06:00  16531.0  16531.0  16524.5  16527.9  130.774        NaN   
2022-11-27 15:07:00  16527.9  16533.2  16527.0  16528.0  132.913        NaN   
2022-11-27 15:08:00  16528.3  16534.6  16528.3  16530.4   73.278        NaN   
2022-11-27 15:09:00  16531.6  16569.4  16531.6  16569.4  171.937        NaN   
2022-11-27 15:10:00  16569.4  16569.4  16535.3  16542.6  127.277        NaN   
2022-11-27 15:11:00  16542.8  16548.3  16540.6  16548.3  231.077        NaN   
2022-11-27 15:12:00  16543.1  16548.3  16538.5  16538.7   89.848        NaN   
2022-11-27 15:13:00  16542.6  16544.8  16540.5  16541.8  106.687        NaN   
2022-11-27 15:14:00  16542.8  16546.6  16541.8  16546.4   68.418        NaN   
2022-11-27 15:15:00  16543.0  16548.2  16541.8  16543.2  111.731        NaN   
2022-11-27 15:16:00  16543.2  16548.7  16543.2  16543.2  121.922        NaN   
2022-11-27 15:17:00  16543.2  16550.7  16543.2  16547.9   58.536        NaN   
2022-11-27 15:18:00  16548.4  16595.9  16548.4  16557.1  182.054        NaN   
2022-11-27 15:19:00  16557.1  16609.2  16554.4  16561.7  188.335        NaN   
2022-11-27 15:20:00  16561.7  16600.0  16557.4  16561.9   99.344        NaN   
2022-11-27 15:21:00  16561.9  16600.0  16558.5  16561.5  137.997  -0.368288   
2022-11-27 15:22:00  16559.0  16562.4  16552.0  16558.1  156.793  -1.176517   
2022-11-27 15:23:00  16554.4  16562.2  16553.0  16554.1   89.274  -1.700036   
2022-11-27 15:24:00  16554.1  16563.3  16552.5  16563.3   60.184   0.646147   
2022-11-27 15:25:00  16553.9  16558.7  16553.9  16555.4  115.378  -1.145732   
2022-11-27 15:26:00  16552.5  16553.7  16548.4  16553.1   38.883  -1.366206   
2022-11-27 15:27:00  16554.3  16554.3  16550.5  16554.0   88.493  -0.654035   
2022-11-27 15:28:00  16557.1  16557.1  16552.8  16554.7   65.199  -0.205182   
2022-11-27 15:29:00  16553.0  16553.9  16547.1  16547.1   41.800  -1.573557   
2022-11-27 15:30:00  16549.2  16553.7  16547.1  16553.7  116.052   0.312838   
2022-11-27 15:31:00  16553.7  16556.1  16550.4  16556.1   83.668   0.794946   
2022-11-27 15:32:00  16556.1  16556.1  16554.0  16555.0   62.783   0.200890   
2022-11-27 15:33:00  16555.0  16557.3  16554.0  16556.1  104.330   0.198362   
2022-11-27 15:34:00  16557.3  16570.0  16557.3  16563.8  122.019   1.505277   
2022-11-27 15:35:00  16561.4  16564.1  16555.2  16562.0  396.884   0.434420   
2022-11-27 15:36:00  16564.5  16570.1  16562.0  16568.1  143.830   1.132165   
2022-11-27 15:37:00  16568.1  16570.1  16568.1  16568.1  131.478   0.458236   
2022-11-27 15:38:00  16569.5  16569.9  16562.0  16569.3  164.463   0.183639   
2022-11-27 15:39:00  16569.3  16569.3  16567.1  16569.3   90.638  -0.153492   
2022-11-27 15:40:00  16569.3  16575.0  16567.3  16575.0   58.460   0.759408   
2022-11-27 15:41:00  16571.5  16575.0  16569.7  16575.0   37.169   0.235740   
2022-11-27 15:42:00  16574.0  16576.5  16571.5  16571.5   79.852  -0.854083   
2022-11-27 15:43:00  16572.9  16576.5  16565.6  16569.1  256.946  -1.224650   
2022-11-27 15:44:00  16569.1  16571.1  16556.5  16560.1   97.140  -2.547835   
2022-11-27 15:45:00  16560.2  16566.4  16557.1  16562.1  174.425  -1.119613   
2022-11-27 15:46:00  16562.3  16566.6  16558.0  16564.9   39.143   0.089759   
2022-11-27 15:47:00  16562.0  16566.0  16562.0  16566.0  100.239   0.360832   
2022-11-27 15:48:00  16566.0  16569.5  16562.3  16568.4   56.307   0.637973   
2022-11-27 15:49:00  16567.9  16567.9  16562.3  16566.6   80.626  -0.04618

In [21]:
test_trader.start_trading()

executing prepare_recent_data
80
executing stablish_initial_position
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kan

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.executing update_position
klast = self.kline_tlast /// klast = 2022-11-27 16:21:00
kprev = (self.kline_tlast - td) /// kprev = 2022-11-27 16:20:00
executing execute_trades
executing report_trade


----------------------------------------------------------------------------------------------------
2022-11-27 16:22:01.0

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

...

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

In [7]:
#test_trader.stop_ses()

In [8]:
#test_trader.twm.stop()

In [9]:
test_trader.orders

NameError: name 'test_trader' is not defined

In [ ]:
test_trader.run_end_time_utc

In [16]:
test_trader.trade_start_time_utc

complete=False --- continuying the ws data retrieval till next complete=True kandle


datetime.datetime(2022, 11, 27, 14, 1, 59, 97414)

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

...

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next complete=True kandle
.complete=False --- continuying the ws data retrieval till next c

In [23]:
test_trader.emergency_price_chg_flag

False

In [24]:
test_trader.close_pair

[]

In [25]:
test_trader.decrease_counter

0

In [26]:
test_trader.increase_counter

0

In [27]:
test_trader.emergency_msg

In [28]:
test_trader.kline_tlast

Timestamp('2022-11-27 22:20:00')

In [29]:
test_trader.kline_tprev_complete

Timestamp('2022-11-27 22:18:00')

In [ ]:
test_trader.pu_price_chg

In [ ]:
##pip install python-binance==1.0.15

In [ ]:
#pip install ta